In [1]:
%load_ext autoreload
%autoreload 2

In [1]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("working dir:", workding_dir)

workding dir: c:\Users\HT\Documents\URP\logical-reasoning


In [2]:
need_to_setup_env = False
need_to_setup_env

False

In [3]:
if need_to_setup_env:
    %pip install -r requirements.txt

In [12]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env.qwen2_7b")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: c:\Users\HT\Documents\URP\logical-reasoning\.env.qwen2_7b


True

In [14]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path, use_english_datasets)

Qwen/Qwen2-7B None False datasets/mgtv results/mgtv-results_qwen2_7b.csv False


In [19]:
import pandas as pd
df = pd.read_csv("datasets/mgtv/train.csv")
df.head()

text label  answer       title  \
0             偷的人信神吗    不是     NaN  乡村之谜：消失的南瓜   
1        偷南瓜是为了来年丰收吗    不是     NaN  乡村之谜：消失的南瓜   
2         村庄里的人喜欢南瓜嘛   不重要     NaN  乡村之谜：消失的南瓜   
3  村庄里的人每年都需要用南瓜做祭品嘛    不是     NaN  乡村之谜：消失的南瓜   
4           是村里的人偷的么     是     NaN  乡村之谜：消失的南瓜   

                                              puzzle  \
0  在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民...   
1  在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民...   
2  在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民...   
3  在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民...   
4  在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民...   

                                               truth  
0  真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季...  
1  真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季...  
2  真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季...  
3  真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季...  
4  真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季...

In [20]:
dataset_data = [
    {
        "instruction": "你是一个逻辑游戏的主持人。游戏规则如下：1. 参与者会得到一个谜题。2. 参与者可以通过提问来获取线索，尝试解开谜题。3. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。4. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。5. 参与者需要根据回答来推理，并最终找出谜题的正确答案。请严格按照这些规则回答参与者提出的问题。谜题: {}实际情况: {}参与者提出的问题: {}",
        "input": "谜题: " + row_dict["title"] + " " + row_dict["puzzle"] + "实际情况: " + row_dict["truth"] + "参与者提出的问题: " + row_dict["text"],
        "output": row_dict["label"]
    }
    for row_dict in df.to_dict(orient="records")
]

dataset_data[0]

{'instruction': '你是一个逻辑游戏的主持人。游戏规则如下：1. 参与者会得到一个谜题。2. 参与者可以通过提问来获取线索，尝试解开谜题。3. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。4. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。5. 参与者需要根据回答来推理，并最终找出谜题的正确答案。请严格按照这些规则回答参与者提出的问题。谜题: {}实际情况: {}参与者提出的问题: {}',
 'input': '谜题: 乡村之谜：消失的南瓜 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。实际情况: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。参与者提出的问题: 偷的人信神吗',
 'output': '不是'}

In [ ]:
import os
import json

# Define the directory where you want to save the JSON file
output_dir = "/content/LLaMA-Factory/data/"

# Ensure the directory exists
os.makedirs(output_dir, exist_ok=True)

# Define the full path for the JSON file
json_file_path = os.path.join(output_dir, "mgtv_train.json")

# Save the dataset data to the specified path
with open(json_file_path, "w") as f:
   json.dump(dataset_data, f)

print(f"JSON file saved to {json_file_path}")


JSON file saved to /content/LLaMA-Factory/data/mgtv_train.json


In [ ]:
import json
%cd /content/LLaMA-Factory/

args = dict(
  model_name_or_path="Qwen/Qwen2-7B", # use Qwen/Qwen2-7B-Instruct model

  stage="sft",                        # do supervised fine-tuning
  do_train=True,
  finetuning_type="lora",                   # use LoRA adapters to save memory
  lora_target="all",                     # attach LoRA adapters to all linear layers
  quantization_bit=4,
  loraplus_lr_ratio=16.0,                   # 16x base LoRA learning rate

  dataset="mgtv_train",
  template="qwen",
  cutoff_len=4096,
  max_samples=5000,
  overwrite_cache="true",
  preprocessing_num_workers=16,

  output_dir="/content/qwen2-7b",
  logging_steps=562,
  save_steps=562,
  plot_loss="true",
  overwrite_output_dir="true",

  per_device_train_batch_size=1,               # the batch size
  gradient_accumulation_steps=8,               # the gradient accumulation steps
  learning_rate=0.001,                     # the learning rate
  num_train_epochs=6.0,                    # the epochs of training
  lr_scheduler_type="cosine",                 # use cosine learning rate scheduler
  warmup_ratio=0.1,                      # use warmup scheduler
  bf16=True,
  ddp_timeout=180000000,                  #5.71 years lol

  val_size=0.1,
  per_device_eval_batch_size=1,
  eval_strategy="steps",
  eval_steps=562,

  report_to="wandb",
)

with open("train_qwen2_7b.json", "w", encoding="utf-8") as f:
  json.dump(args, f, indent=2)

/content/LLaMA-Factory


In [ ]:
with open("data/dataset_info.json", 'r+') as file:
    # First we load existing data into a dict.
    file_data = json.load(file)
    # Insert new_data at the beginning of the emp_details list.
    qwen2_7b = {"mgtv_train": {
        "file_name": "mgtv_train.json"
      }
    }

    qwen2_7b.update(file_data)
    file.seek(0)
    # convert back to json.
    json.dump(qwen2_7b, file, indent=2)

In [ ]:
!llamafactory-cli train train_qwen2_7b.json

2024-07-15 14:34:28.658348: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-07-15 14:34:28.710574: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-15 14:34:28.710630: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-15 14:34:28.712064: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-07-15 14:34:28.719927: I tensorflow/core/platform/cpu_feature_guar

In [ ]:
import shutil
shutil.move("/content/qwen2-7b", "/content/drive/MyDrive/runs")

'/content/drive/MyDrive/runs/qwen2-7b'

In [ ]:
import shutil
shutil.move("/content/drive/MyDrive/runs", "/content/qwen2-7b", )

'/content/qwen2-7b'

In [ ]:
def evaluate_model_all_epochs(model_name, adapter_path_base, num_train_epochs, start_epoch=0, load_in_4bit=True, num_of_entries=-1):
    os.environ["MODEL_NAME"] = model_name
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    for i in range(start_epoch, num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{562 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path

        !python llm_toolkit/eval_logical_reasoning.py {num_of_entries}

In [ ]:
%%time

evaluate_model_all_epochs("Qwen/Qwen2-7B", "/content/qwen2-7b/qwen2-7b", 4, start_epoch=0, load_in_4bit=False, num_of_entries=-1)

Epoch 0
loading env vars from: /content/drive/.shortcut-targets-by-id/1E09lTnfbsjtTgQg65dQ3y9D2R6l8waxR/logical-reasoning/.env
Adding /content/drive/.shortcut-targets-by-id/1E09lTnfbsjtTgQg65dQ3y9D2R6l8waxR/logical-reasoning to sys.path
2024-07-16 03:59:05.588323: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-07-16 03:59:05.639368: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-16 03:59:05.639412: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-16 03:59:05.640960: E external/local_xla